### 0852617 曾鈺評 機器學習HW02_1

In [1]:
import numpy as np
import gzip
import matplotlib.pyplot as plt
import math

In [2]:
directory = "D:\\1091NCTU\Machine learning\\Homework\\"
IMAGE_SIZE = 28
NUM_TRAIN_IMAGES = 60000
NUM_TEST_IMAGES = 10000
NUM_CHANNELS = 1

In [3]:
def ReadData(filename, num_char, num_images, path=directory, image_size=IMAGE_SIZE, num_channels=NUM_CHANNELS):
    with gzip.open(directory+filename) as file:
        file.read(num_char)
        buf = file.read(num_images * image_size * image_size * num_channels)
        data = np.frombuffer(buf, dtype=np.uint8).astype(np.int)
    return data

In [4]:
def Prior(training_Y):
    prior = np.zeros(10)
    for i in range(10):
        prior[i] = np.sum(training_Y == i) / 60000
    return prior

In [5]:
def DiscreteMode(training_X, training_Y, test_X):
    num_pixel_bin = np.zeros((10, 28*28, 32))
    num_pixel = np.zeros((10, 28*28))
    num = np.zeros(10)
    for i in range(10):
        num[i] = training_X[training_Y == i].shape[0]
        for j in range(28*28):
            for k in range(32):
                num_pixel_bin[i][j][k] = np.sum(training_X[training_Y == i, j] == k) / num[i]

    # 計算補0的probability
    pseudo_prob = num_pixel_bin[num_pixel_bin != 0].min()
    num_pixel_bin_new = num_pixel_bin.copy()
    num_pixel_bin_new[num_pixel_bin_new == 0] = pseudo_prob
    #0.0001483239394838327
    
    #計算10000筆資料在0~9分別的posterior (尚未加上prior)
    likelihood_discrete = np.zeros((10000,10))
    for n in range(10000):
        for i in range(10):
            likelihood_discrete[n][i] = np.log(num_pixel_bin_new[i][range(28*28),test_X[n]]).sum()
    return num_pixel_bin, likelihood_discrete

In [6]:
def ContinuousMode(training_X, training_Y, test_X, epsilon=2000):
    mu = np.zeros((10, 784))
    variance = np.zeros((10, 784))
    gaussian_prob = np.zeros((10000,10,784))
    for i in range(10):
        for j in range(28*28):
            mu[i][j] = training_X[training_Y == i,j].mean()
            variance[i][j] = np.var(training_X[training_Y == i,j])
    variance[variance == 0] = epsilon

    for i in range(10):
        for j in range(28*28):
            gaussian_prob[:,i,j] = -0.5 * np.log(2*np.pi*variance[i][j]) - 0.5 * (test_X[:,j] - mu[i][j])**2 / variance[i][j]

    likelihood_gaussian = np.sum(gaussian_prob, axis=2)
    return mu, likelihood_gaussian

In [7]:
def Posterior(likelihood, prior):
    posterior_temp = likelihood + np.log(prior)
    posterior = (posterior_temp.T / posterior_temp.sum(axis=1).T).T
    pred_Y = np.argmin(posterior, axis=1)
    return posterior, pred_Y

In [8]:
def PrintPosterior(posterior, pred_Y, test_Y):
    for n in range(10000):
        print("Posterior (in log scale):")
        for i in range(10):
            print("%s: %s" %(i, posterior[n,i]))
        print("Prediction: %s, Ans: %s\n" %(pred_Y[n], test_Y[n]))

In [9]:
def PrintImagination(images, toggle):
    print("Imagination of numbers in Bayesian classifier:")
    if toggle == 0:
        for i in range(10):
            print("%s:" %i)
            for j in range(28*28):
                if j % 28 == 27:
                    print((np.argmax(images[i], axis=1) >= 16)[j].astype(int))
                else:
                    print((np.argmax(images[i], axis=1) >= 16)[j].astype(int), end=' ')
            print("\n")
    if toggle == 1:
        for i in range(10):
            print("%s:" %i)
            for j in range(28*28):
                if j % 28 == 27:
                    print((images[i] >= 128)[j].astype(int))
                else:
                    print((images[i] >= 128)[j].astype(int), end=' ')
            print("\n")

In [10]:
training_X = ReadData(filename="train-images-idx3-ubyte.gz", num_char=16, num_images=NUM_TRAIN_IMAGES)
training_Y = ReadData(filename="train-labels-idx1-ubyte.gz", num_char=8, num_images=NUM_TRAIN_IMAGES)
test_X = ReadData(filename="t10k-images-idx3-ubyte.gz", num_char=16, num_images=NUM_TRAIN_IMAGES)
test_Y = ReadData(filename="t10k-labels-idx1-ubyte.gz", num_char=8, num_images=NUM_TRAIN_IMAGES)

training_X = training_X.reshape(NUM_TRAIN_IMAGES, IMAGE_SIZE * IMAGE_SIZE)
test_X = test_X.reshape(NUM_TEST_IMAGES, IMAGE_SIZE * IMAGE_SIZE)

In [16]:
def NaiveBayes_Discrete(training_X=training_X, training_Y=training_Y, test_X=test_X, text_Y=test_Y):
    prior = Prior(training_Y)
    training_X = (training_X / 8).astype(int)
    test_X = (test_X / 8).astype(int)
    num_pixel_bin, likelihood = DiscreteMode(training_X, training_Y, test_X)
    posterior, pred_Y = Posterior(likelihood, prior)
    PrintPosterior(posterior, pred_Y, test_Y)
    PrintImagination(num_pixel_bin, toggle)
    print("Error rate: %.4f" %(1 - np.mean(pred_Y == test_Y)))

In [17]:
def NaiveBayes_Continuous(training_X=training_X, training_Y=training_Y, test_X=test_X, text_Y=test_Y):
    prior = Prior(training_Y)
    mu, likelihood = ContinuousMode(training_X, training_Y, test_X)
    posterior, pred_Y = Posterior(likelihood, prior)
    PrintPosterior(posterior, pred_Y, test_Y)
    PrintImagination(mu, toggle)
    print("Error rate: %.4f" %(1 - np.mean(pred_Y == test_Y)))

In [22]:
toggle = int(input("Toggle = "))
prior = Prior(training_Y)
if toggle == 0:
    NaiveBayes_Discrete()
elif toggle == 1:
    NaiveBayes_Continuous()

Toggle = 0
Posterior (in log scale):
0: 0.11102371833398983
1: 0.11872800839700827
2: 0.10514140049586974
3: 0.09995174193620696
4: 0.09371288140834357
5: 0.09739452626609077
6: 0.11487087942054842
7: 0.07399026002521297
8: 0.09948671705886925
9: 0.08569986665786014
Prediction: 7, Ans: 7

Posterior (in log scale):
0: 0.09994145239467879
1: 0.10782614752951587
2: 0.08282577843482304
3: 0.09011731761429465
4: 0.10887891568691051
5: 0.09239531157492238
6: 0.08944531216310722
7: 0.11925125932447377
8: 0.0962669943936534
9: 0.11305151088362039
Prediction: 2, Ans: 2

Posterior (in log scale):
0: 0.1289499897503159
1: 0.06355583746729922
2: 0.09853655127272243
3: 0.10053422008906256
4: 0.10340875656972809
5: 0.09649919519700596
6: 0.10337406896035466
7: 0.10182067475173893
8: 0.10023724405543835
9: 0.10308346188633387
Prediction: 1, Ans: 1

Posterior (in log scale):
0: 0.07732981936670619
1: 0.1426752466117244
2: 0.09674936648190739
3: 0.09623655219433362
4: 0.10133998460300947
5: 0.092350538